In [1]:
import sys
sys.path.append('..')
from osp import *

In [3]:
JSTOR_STASH

LMDBHashStash(~/.cache/hashstash/osp_jstor/lmdb.hashstash.lz4+b64/data.db)

In [80]:
PMLA_STASH = HashStash('osp_pmla')
PMLA_STASH

LMDBHashStash(~/.cache/hashstash/osp_pmla/lmdb.hashstash.lz4+b64/data.db)

In [5]:
df_pmla = get_pmla_df().set_index('id')

100%|██████████| 71902/71902 [00:04<00:00, 16271.02it/s]


In [6]:
df_jstor = get_jstor_data().set_index('id')

In [29]:
import random

def collect_tree_stats(stash, limit=None):
    all_tree_stats = []
    for id,docstr in tqdm(stash.items(),total=len(stash) if limit is None else limit):
        doc = stanza.Document.from_serialized(docstr)
        tree_stats = pd.DataFrame(get_tree_stats(sent) for sent in doc.sentences)
        tree_stats['id'] = id
        all_tree_stats.append(tree_stats)
        if limit is not None and len(all_tree_stats) >= limit:
            break
    all_tree_stats = pd.concat(all_tree_stats)
    for col in all_tree_stats.columns:
        if col not in ['id','num_words']:
            all_tree_stats[col+'_per_10words'] = all_tree_stats[col] / all_tree_stats['num_words'] * 10
    return all_tree_stats

In [78]:
def get_pmla_tree_df(limit=None):
    df_pmla = get_pmla_df().set_index('id')
    all_tree_stats = collect_tree_stats(PMLA_STASH, limit=limit)
    df_all_tree_stats = all_tree_stats.merge(df_pmla, on='id', how='left')
    return df_all_tree_stats

In [81]:
df_pmla_tree = get_pmla_tree_df()

100%|██████████| 930/930 [08:17<00:00,  1.87it/s]


In [32]:
def get_jstor_tree_df(limit=None):
    df_jstor = get_jstor_data().set_index('id')
    all_tree_stats = collect_tree_stats(JSTOR_STASH, limit=limit)
    df_all_tree_stats = all_tree_stats.merge(df_jstor, on='id', how='left')
    return df_all_tree_stats

In [45]:
df_jstor_tree = get_jstor_tree_df(limit=None)

100%|██████████| 6062/6062 [1:23:10<00:00,  1.21it/s]  


In [82]:
df_combined = pd.concat([df_pmla_tree.assign(discipline='Literature'), df_jstor_tree.assign(discipline='Philosophy')])

In [83]:
df_combined.groupby(['discipline','decade'])['id'].nunique()

discipline  decade
Literature  1900       79
            1910       78
            1920       78
            1930       77
            1940       78
            1950       78
            1960       77
            1970       77
            1980       77
            1990       77
            2000       77
            2010       77
Philosophy  1880       26
            1890      360
            1900      378
            1910      390
            1920      413
            1930      433
            1940      444
            1950      453
            1960      445
            1970      453
            1980      457
            1990      453
            2000      454
            2010      460
            2020      443
Name: id, dtype: int64

In [84]:
for k in df_combined:
    if k.endswith('per_10words'):
        df_combined[k.replace('per_10words','per_100words')] = df_combined[k] * 10
df_combined = df_combined.drop(columns=['height_per_10words','height_per_100words'])
odf = df_combined.groupby(['discipline','decade']).mean(numeric_only=True)
# odf

In [85]:
odf = df_combined.groupby(['discipline','decade']).mean(numeric_only=True)
figdf = odf.drop(columns=['year','publicationYear','wordCount','pageCount']).reset_index().melt(id_vars=['decade','discipline'])
figdf = figdf[(figdf['variable'].isin(['num_words','height'])) | ~figdf['variable'].str.contains('per_10')]
figdf

decade  discipline          variable      value
0      1900  Literature         num_words  30.599872
1      1910  Literature         num_words  29.970409
2      1920  Literature         num_words  30.091842
3      1930  Literature         num_words  31.794830
4      1940  Literature         num_words  31.562157
..      ...         ...               ...        ...
373    1980  Philosophy  num_words_adverb   2.153426
374    1990  Philosophy  num_words_adverb   2.113162
375    2000  Philosophy  num_words_adverb   2.152455
376    2010  Philosophy  num_words_adverb   2.096551
377    2020  Philosophy  num_words_adverb   2.093321

[378 rows x 4 columns]

In [86]:
# !pip install plotnine
import plotnine as p9
p9.options.figure_size = (14, 10)
fig = p9.ggplot(figdf, p9.aes(x='decade', y='value', color='discipline')) + p9.geom_point() + p9.geom_line() + p9.theme_minimal() + p9.facet_wrap('variable', scales='free')
fig

In [60]:
# df_jstor_tree.iloc[0]
s=(df_jstor_tree.groupby(['is_part_of','decade'])['id'].nunique() >= 25)
ok = set(s[s].index)
# ok

In [88]:
df_jstor_tree.is_part_of.value_counts()

is_part_of
Synthese                                       404310
The Philosophical Review                       203363
Canadian Journal of Philosophy                 184499
International Journal of Ethics                154185
The Journal of Philosophy                      138407
Erkenntnis (1975-)                             124603
Philosophy and Phenomenological Research       119683
Proceedings of the Aristotelian Society        117359
Dialectica                                      96468
The Review of Metaphysics                       81548
Ethics                                          75121
Erkenntnis (1930-1938)                          34324
Research in Phenomenology                       16632
The Journal of Unified Science (Erkenntnis)      1673
Name: count, dtype: int64

In [91]:
p9.options.figure_size = (16, 9)
p9.options.dpi = 300
# odf = df_jstor_tree[df_jstor_tree['is_part_of'].isin({'Synthese','The Philosophical Review'})].groupby(['is_part_of','decade']).mean(numeric_only=True).reset_index()
odf = df_jstor_tree.groupby(['is_part_of','decade']).mean(numeric_only=True).reset_index()
odf['filter'] = list(zip(odf['is_part_of'], odf['decade']))
# filter to only include journals with at least 10 articles per decade
odf = odf[odf['filter'].isin(ok)]
odf

is_part_of  decade  num_words     height  \
0    Canadian Journal of Philosophy    1970  30.391495  13.999854   
1    Canadian Journal of Philosophy    1980  30.539813  14.184081   
2    Canadian Journal of Philosophy    1990  29.272813  13.930922   
3    Canadian Journal of Philosophy    2000  29.914682  14.012709   
4    Canadian Journal of Philosophy    2010  27.443147  13.415964   
..                              ...     ...        ...        ...   
91         The Philosophical Review    1970  31.105953  14.480214   
97        The Review of Metaphysics    1950  29.133300  13.116328   
98        The Review of Metaphysics    1960  29.297942  13.580874   
99        The Review of Metaphysics    1970  31.157041  14.061481   
101       The Review of Metaphysics    1990  33.180058  13.905586   

     num_independent_clauses  num_dependent_clauses  \
0                   1.582931               1.458863   
1                   1.625606               1.476804   
2                   1.580851               1.340680   
3                   1.578903               1.426541   
4                   1.428957               1.283902   
..                       ...                    ...   
91                  1.695834               1.584774   
97                  1.537161               1.119723   
98                  1.596897               1.301484   
99                  1.609348               1.355793   
101                 1.540886               1.210476   

     num_words_in_dependent_clauses  num_words_in_independent_clauses  \
0                         22.579534                          7.811961   
1                         22.105740                          8.434073   
2                         19.801136                          9.471677   
3                         21.308272                          8.606410   
4                         18.781066                          8.662081   
..                              ...                               ...   
91                        24.583266                          6.522688   
97                        16.737006                         12.396294   
98                        18.500422                         10.797521   
99                        21.221471                          9.935571   
101                       19.684601                         13.495457   

     num_punct  num_punct_colon  ...  num_punct_comma_per_10words  \
0     3.334612         0.134882  ...                     0.434713   
1     3.435194         0.165749  ...                     0.451239   
2     3.322300         0.169533  ...                     0.464116   
3     3.430113         0.201691  ...                     0.470931   
4     3.406621         0.224709  ...                     0.467310   
..         ...              ...  ...                          ...   
91    3.527794         0.138795  ...                     0.446968   
97    3.319921         0.210169  ...                     0.482964   
98    3.266993         0.195902  ...                     0.477656   
99    3.674471         0.253902  ...                     0.500785   
101   4.095441         0.382713  ...                     0.520592   

     num_parens_per_10words  num_words_noun_per_10words  \
0                  0.181415                    2.233580   
1                  0.183970                    2.249092   
2                  0.173628                    2.342905   
3                  0.183632                    2.370873   
4                  0.213735                    2.495699   
..                      ...                         ...   
91                 0.205439                    2.156401   
97                 0.116183                    2.349452   
98                 0.125680                    2.220553   
99                 0.150617                    2.271884   
101                0.146454                    2.410748   

     num_words_adjective_per_10words  num_words_verb_per_10words  \
0                           0.903827                

In [92]:
figdf = odf.drop(columns=['year','contributed_content','review_required','filter']).melt(id_vars=['decade','is_part_of'])
figdf = figdf[(figdf['variable'] == 'num_words') | ~figdf['variable'].str.contains('per_10word')]
fig = p9.ggplot(
    figdf, 
    p9.aes(x='decade', y='value', color='is_part_of')
) + p9.geom_point() + p9.geom_line() + p9.theme_minimal() + p9.facet_wrap('variable', scales='free', nrow=3) + p9.labs(color='Journal', title='Syntactic statistics')
fig.save('../figures/jstor_syntactic_stats.png')
fig

In [ ]:
# df_combined.groupby(['discipline','decade'])['id'].nunique()


MultiIndex([(1880,  'Proceedings of the Aristotelian Society'),
            (1890,          'International Journal of Ethics'),
            (1890,  'Proceedings of the Aristotelian Society'),
            (1890,                 'The Philosophical Review'),
            (1900,          'International Journal of Ethics'),
            (1900,  'Proceedings of the Aristotelian Society'),
            (1900,                 'The Philosophical Review'),
            (1910,          'International Journal of Ethics'),
            (1910,  'Proceedings of the Aristotelian Society'),
            (1910,                 'The Philosophical Review'),
            (1920,          'International Journal of Ethics'),
            (1920,  'Proceedings of the Aristotelian Society'),
            (1920,                'The Journal of Philosophy'),
            (1920,                 'The Philosophical Review'),
            (1930,                   'Erkenntnis (1930-1938)'),
            (1930,                      

In [16]:
# !pip install plotnine
import plotnine as p9
p9.options.figure_size = (10, 10)

